<a href="https://colab.research.google.com/github/Lewislou/Pytorch-pratical-Learning/blob/master/Exercise5.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# Execute this code block to install dependencies when running on colab
try:
    import torch
except:
    from os.path import exists
    from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
    platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())
    cuda_output = !ldconfig -p|grep cudart.so|sed -e 's/.*\.\([0-9]*\)\.\([0-9]*\)$/cu\1\2/'
    accelerator = cuda_output[0] if exists('/dev/nvidia0') else 'cpu'

    !pip install -q http://download.pytorch.org/whl/{accelerator}/torch-1.0.0-{platform}-linux_x86_64.whl torchvision

try: 
    import torchbearer
except:
    !pip install torchbearer

In [0]:
# automatically reload external modules if they change
%load_ext autoreload
%autoreload 2

import torch
import torch.nn.functional as F
import torchvision.transforms as transforms
import torchbearer
from torch import nn
from torch import optim
from torch.utils.data import DataLoader
from torchvision.datasets import MNIST
from torchbearer import Trial

In [0]:
import torch
from torchvision import transforms
from torch.utils.data import Dataset

class MyDataset(Dataset):
  def __init__(self, size=5000, dim=40, random_offset=0):
        super(MyDataset, self).__init__()
        self.size = size
        self.dim = dim
        self.random_offset = random_offset

  def __getitem__(self, index):
      if index >= len(self):
          raise IndexError("{} index out of range".format(self.__class__.__name__))

      rng_state = torch.get_rng_state()
      torch.manual_seed(index + self.random_offset)

      while True:
        img = torch.zeros(self.dim, self.dim)
        dx = torch.randint(-10,10,(1,),dtype=torch.float)
        dy = torch.randint(-10,10,(1,),dtype=torch.float)
        c = torch.randint(-20,20,(1,), dtype=torch.float)

        params = torch.cat((dy/dx, c))
        xy = torch.randint(0,img.shape[1], (20, 2), dtype=torch.float)
        xy[:,1] = xy[:,0] * params[0] + params[1]

        xy.round_()
        xy = xy[ xy[:,1] > 0 ]
        xy = xy[ xy[:,1] < self.dim ]
        xy = xy[ xy[:,0] < self.dim ]

        for i in range(xy.shape[0]):
          x, y = xy[i][0], self.dim - xy[i][1]
          img[int(y), int(x)]=1
        if img.sum() > 2:
          break

      torch.set_rng_state(rng_state)
      return img.unsqueeze(0), params

  def __len__(self):
      return self.size

train_data = MyDataset()
val_data = MyDataset(size=500, random_offset=33333)
test_data = MyDataset(size=500, random_offset=99999)

In [0]:
# create data loaders
trainloader = DataLoader(train_data, batch_size=128, shuffle=True)
valloader = DataLoader(val_data, batch_size=128, shuffle=True)
testloader = DataLoader(test_data, batch_size=128, shuffle=True)

In [5]:
data,weight = train_data[2]
data.size()
weight

tensor([1.5000, 1.0000])

In [0]:
from torch.autograd import Variable
for i, data in enumerate(trainloader):
  sample, target = data
  # set data as cuda varibale
  sample = Variable(sample.float().cuda())
  target = Variable(target.cuda())
  print(sample.data.size(), "labels", target.data.size())

torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) labels torch.Size([128, 2])
torch.Size([128, 1, 40, 40]) la

In [6]:
sample.size(),target

NameError: ignored

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [0]:
import torch 
import torch.nn.functional as F
from torch import nn

# Model Definition
class CNNbaseline(nn.Module):
    def __init__(self):
        super(CNNbaseline, self).__init__()
        self.conv1 = nn.Conv2d(1, 48, (3, 3), stride = 1,padding=1)
        self.fc1 = nn.Linear(48 * 20**2, 128)
        self.fc2 = nn.Linear(128, 2)
    
    def forward(self, x):
        out = self.conv1(x)
        out = F.relu(out)
        out = F.max_pool2d(out, (2,2))
        out = F.dropout(out, 0.2)
        out = out.view(out.shape[0], -1)
        out = self.fc1(out)
        out = F.relu(out)
        out = self.fc2(out)
        return out

In [9]:
# build the model
model = CNNbaseline()

# define the loss function and the optimiser
loss_function = nn.MSELoss()
optimiser = optim.Adam(model.parameters())

device = "cuda:0" if torch.cuda.is_available() else "cpu"
trial = Trial(model, optimiser, loss_function, metrics=['loss', 'accuracy']).to(device)
trial.with_generators(trainloader,val_generator=valloader, test_generator=testloader)
trial.run(epochs=100)
results = trial.evaluate(data_key=torchbearer.TEST_DATA)
print(results)
#save the trained model weights
torch.save(model.state_dict(), "./CNNbaseline.weights")


{'test_loss': 6.3885087966918945, 'test_mse': 6.3765764236450195}


In [23]:
test_data.size
plt.scatter(x.data.numpy(), y.data.numpy())

plt.plot(x.data.numpy(), prediction.data.numpy(), 'r-', lw=5)


500

In [25]:
from PIL import Image
import matplotlib.pyplot as plt
for i in range(test_data.size):
  data,label = test_data[i]
  print(data.size())
  traindata = data.to(device)
  prediction = model(traindata.unsqueeze(0))
  plt.plot(data.data.numpy(), prediction.data.numpy(), 'r-', lw=5)
  print(prediction.size())

  

torch.Size([1, 40, 40])


TypeError: ignored

Task2:

In [0]:
import torch 
import torch.nn.functional as F
from torch import nn

# Model Definition
class simpleCNN(nn.Module):
    def __init__(self):
        super(simpleCNN, self).__init__()
        self.conv1 = nn.Conv2d(1, 48, (3, 3), stride = 1,padding=1)
        self.conv2 = nn.Conv2d(48, 48, (3, 3), stride = 1,padding=1)
        self.fc1 = nn.Linear(48 * 1**2, 128)
        self.fc2 = nn.Linear(128, 2)
    
    def forward(self, x):
        out = self.conv1(x)
        out = F.relu(out)
        out = F.max_pool2d(out, (2,2))
        out = self.conv2(out)
        out = F.relu(out)
        out = F.max_pool2d(out, (2,2))
        out = F.dropout(out, 0.2)
        out = F.adaptive_max_pool2d(out,(1,1))
        out = out.view(out.shape[0], -1)
        out = self.fc1(out)
        out = F.relu(out)
        out = self.fc2(out)
        return out

In [0]:
# build the model
model = simpleCNN()

# define the loss function and the optimiser
loss_function = nn.BCELoss()
optimiser = optim.Adam(model.parameters())

device = "cuda:0" if torch.cuda.is_available() else "cpu"
trial = Trial(model, optimiser, loss_function, metrics=['loss', 'accuracy']).to(device)
trial.with_generators(trainloader,val_generator=valloader, test_generator=testloader)
trial.run(epochs=100)
results = trial.evaluate(data_key=torchbearer.TEST_DATA)
print(results)


{'test_loss': nan, 'test_binary_acc': 0.8770000338554382}


3.1 Let’s regress (

In [0]:
import torch 
import torch.nn.functional as F
from torch import nn

# Model Definition
class expandCNN(nn.Module):
    def __init__(self):
        super(expandCNN, self).__init__()
        self.conv1 = nn.Conv2d(3, 48, (3, 3), stride = 1,padding=1)
        self.conv2 = nn.Conv2d(48, 48, (3, 3), stride = 1,padding=1)
        self.fc1 = nn.Linear(48 * 1**2, 128)
        self.fc2 = nn.Linear(128, 2)
    
    def forward(self, x):
        idxx = torch.repeat_interleave(torch.arange(-20,20,dtype=torch.float).unsqueeze(0)/40.0,repeats=40,dim=0).to(x.device) #对第零个维度复制40遍输出40*40
        idxy = idxx.clone().t() #40*40
        idx = torch.stack([idxx,idxy]).unsqueeze(0) #1*2*40*40
        idx = torch.repeat_interleave(idx,repeats=x.shape[0],dim=0)#128*2*40*40
        x = torch.cat([x,idx],dim=1)#128*2*40*40

        out = self.conv1(x)
        out = F.relu(out)
        out = F.max_pool2d(out, (2,2))
        out = self.conv2(out)
        out = F.relu(out)
        out = F.max_pool2d(out, (2,2))
        out = F.dropout(out, 0.2)
        out = F.adaptive_max_pool2d(out,(1,1))
        out = out.view(out.shape[0], -1)
        out = self.fc1(out)
        out = F.relu(out)
        out = self.fc2(out)
        return out

In [0]:
# build the model
model = expandCNN()

# define the loss function and the optimiser
loss_function = nn.BCELoss()
optimiser = optim.Adam(model.parameters())

device = "cuda:0" if torch.cuda.is_available() else "cpu"
trial = Trial(model, optimiser, loss_function, metrics=['loss', 'accuracy']).to(device)
trial.with_generators(trainloader,val_generator=valloader, test_generator=testloader)
trial.run(epochs=100)
results = trial.evaluate(data_key=torchbearer.TEST_DATA)
print(results)


{'test_loss': nan, 'test_binary_acc': 0.8630000352859497}
